In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import select_nodes, to_param_dict, to_param_list, insert_zero_params, rescale_manybody_params
from statmechlib.preprocessing import Trajectory, scale_configuration, pair_dist_cutoff, find_index
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
# stats_file = 'stats_marinica' # 'stats_samples'
# target_file = 'target_marinica' # 'target_samples'
params_file = 'marinica_params'
# stats_file = 'stats_manyknots' # 'stats_samples'
# target_file = 'target_manyknots' # 'target_samples'
# stats_file = 'stats_manymd' # 'stats_samples'
# target_file = 'target_manymd' # 'target_samples'
stats_file = 'stats_manyall' # 'stats_samples'
target_file = 'target_manyall' # 'target_samples'
# stats_file = 'stats_everything' # 'stats_samples'
# target_file = 'target_everything' # 'target_samples'
stats_md_file = 'stats_onlymd' # 'stats_samples'
target_md_file = 'target_onlymd' # 'stats_samples'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)
    
with open(os.path.join(working, stats_md_file+'.pickle'), 'rb') as fi:
    stats_md = pickle.load(fi)
    
with open(os.path.join(working, target_md_file+'.pickle'), 'rb') as fi:
    targets_md = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
def downselect(stats_inp, pair_knots, edens_knots):
    
    # find idices of knots
    pair_index = find_index(pair_knots, stats_inp['hyperparams']['pair'])
    edens_index = find_index(edens_knots, stats_inp['hyperparams']['edens'])
    
    # create boolean arrays with select indices set to True
    p_ix = np.array([True if i in pair_index else False for i in range(len(stats_inp['hyperparams']['pair']))])
    m_ix = np.array([True if i in edens_index else False for i in range(len(stats_inp['hyperparams']['edens']))])

    stats_out = select_nodes(stats_inp, p_ix, m_ix)
    
    return stats_out

In [8]:
pair_knots = [2.22, 2.46, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.5, 2.8663175, 3.1,  3.5,  4.5]

In [9]:
stats = downselect(stats_all, pair_knots, edens_knots)
print(stats['hyperparams'])
stats_select_md = downselect(stats_md, pair_knots, edens_knots)
print(stats_select_md['hyperparams'])

{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}
{u'pair': [2.2200000000000002, 2.46, 2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 2.8663175000000001, 3.1000000000000001, 3.5, 4.5]}


In [10]:
targets['md'] = targets_md['md']
stats['md'] = stats_select_md['md']

In [11]:
for key in sorted(targets.keys()):
    for box, xyz, ene in zip(targets[key]['box'], targets[key]['xyz'], stats[key]['energy']):
        n = len(xyz)
        vol = np.linalg.det(box)
        corr = float(n*n)/vol
        ene.append([corr])

In [12]:
stats['bcc_npt_langevin_300K']['energy'][0][:]

[array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.32452672e-04,   2.40108437e-01,   1.49699018e+01,
          3.67830273e+01,   6.58053659e+01,   2.44033647e+02,
          4.40325883e+02,   6.80111008e+02,   1.13544979e+03,
          1.32771865e+03,   1.53444986e+03,   1.82571708e+03,
          1.89696652e+03,   1.96972937e+03]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          4.37184093e-15,   3.18476767e-07,   2.82775234e-02,
          9.17736776e-01,   9.14748666e+00,   1.69749763e+03,
          1.79543454e+04,   1.02110145e+05,   7.92918644e+05,
          1.48233268e+06,   2.64426772e+06,   5.29910283e+06,
          6.17592659e+06,   7.17934901e+06]),
 array([  0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          9.35076567e-08,   2.01440000e-03,   1.80322649e+00,
          1.06606591e+01,   3.39604107e+01,   4.65546847e+02,
          1.51515052e+03,   3.61420678e+03,   1.00729590e+04,
          1.37729635e+04,   1.83956954e+

In [13]:
targets['eos_fcc']['weight'] = 0.0
targets['bain']['weight'] = 0.0
targets['eos']['weight'] = 0.0
targets['eos_bcc']['weight'] = 0.0
#targets['liq_5000K']['weight'] = 0.1

In [14]:
targets.keys()

['bcc_npt_langevin_3700K',
 'md',
 'vac_npt_langevin_2000K',
 'relax',
 'screw_111_npt_langevin_2000K',
 'bcc_npt_langevin_300K',
 'i111_npt_langevin_2000K',
 'eos',
 'fcc_npt_langevin_300K',
 'eos_fcc',
 'i110_npt_langevin_2000K',
 'liq_3700K',
 'liq_5000K',
 'eos_bcc',
 'bain']

In [15]:
[(key, targets[key]['weight']) for key in targets.keys()]

[('bcc_npt_langevin_3700K', 1.0),
 ('md', 1.0),
 ('vac_npt_langevin_2000K', 1.0),
 ('relax', 1.0),
 ('screw_111_npt_langevin_2000K', 1.0),
 ('bcc_npt_langevin_300K', 1.0),
 ('i111_npt_langevin_2000K', 1.0),
 ('eos', 0.0),
 ('fcc_npt_langevin_300K', 1.0),
 ('eos_fcc', 0.0),
 ('i110_npt_langevin_2000K', 1.0),
 ('liq_3700K', 1.0),
 ('liq_5000K', 1.0),
 ('eos_bcc', 0.0),
 ('bain', 0.0)]

In [16]:
start_params = []
# start_params.append([ -4.18353755e+00,  -9.63668936e-03,  0.0, -1.00171035e+02,
#          1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
#          2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
#          1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
#          1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
#         -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
#          4.64461212e+00,   3.23329113e-01,   5.82061842e-02, -0.1])
# start_params.append([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
#         -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
#         -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
#          2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
#         -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
#          2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
#         -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
#          5.51658454e-02,   1.58601447e+00])
# start_params.append([ -4.16739003e+00,  -4.97036785e-03,  -4.62426912e+02,
#          2.63469650e+02,   1.00253629e+01,   2.05151925e+01,
#         -1.36702712e+01,   2.29129977e+01,  -1.27210473e+01,
#          2.95533783e+00,   8.18470873e-01,  -7.89494754e-01,
#         -8.74455389e-01,   2.10177842e+00,  -9.22682795e-01,
#         -6.93852493e-02,  -1.52166575e+00,   1.40766925e+00,
#          1.52571934e+02,   3.37536873e-01,   6.89310740e-01,
#          4.87102227e-02,   2.79573955e+00])
# start_params.append([ -4.33954858e+00,  -1.02215197e-02,  0.0, -1.12590032e+02,
#          3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
#          2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
#          1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
#          1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
#         -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
#          4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
#          3.46319317e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02,   5.60287637e+00])

# start_params.append([-4.48347382e+00,  -7.78079006e-03,   2.92055760e+02,
#          1.84809430e+02,  -6.18705307e+01,   3.27735461e+01,
#         -1.36588262e+01,   2.11547368e+01,  -5.45394162e+00,
#          8.02998352e-01,   1.21949599e+00,  -9.43034331e-01,
#         -7.71285316e-01,   2.00564540e+00,  -8.93039729e-01,
#         -9.92574423e-03,  -1.55106037e+00,   1.39898785e+00,
#          2.54912062e+02,   3.19484582e+00,  -3.49947883e-01,
#          6.32970386e-02,   4.13612869e+00])

# start_params.append([ -4.41712815e+00,  -7.57807965e-03, 0.0, 2.79276814e+02,
#          1.74479561e+02,  -6.59620942e+01,   3.53977481e+01,
#         -1.40546374e+01,   2.11913467e+01,  -4.95603366e+00,
#          8.26392820e-01,   1.26391280e+00,  -9.48799563e-01,
#         -7.79099318e-01,   2.00268261e+00,  -8.90495881e-01,
#         -8.59210993e-03,  -1.54948191e+00,   1.39577855e+00,
#          2.43904610e+02,   3.47694754e+00,  -3.14999583e-01,
#          6.33069119e-02])

# start_params.append([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
#          3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
#         -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
#         -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
#          7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
#         -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
#          1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
#          2.18327852e+00,   6.63152141e-02, 0.0])

# start_params.append([ -2.95016477e+00,   3.78177969e-04,  -5.21095611e+02,
#          3.09845244e+02,  -4.69222440e+02,   3.95186037e+02,
#         -1.11630659e+02,   5.36915127e+00,   1.52984702e+01,
#         -1.54915170e+01,   7.53107481e+00,  -2.98591742e+00,
#          7.55346307e-01,  -1.00678488e+00,   1.96634582e+00,
#         -8.71560927e-01,  -1.41820832e-01,  -1.46508000e+00,
#          1.42936365e+00,   7.23805795e+01,   0.0, 9.18071460e-01,
#          2.04259992e+00,   6.28575567e-02,   7.62804667e-03])

# start_params.append([ -3.27882058e+00,  -9.77681860e-04,  -5.95486537e+02,
#          3.42401535e+02,  -4.15497479e+02,   3.71316746e+02,
#         -1.07274610e+02,  -2.93282898e+00,   1.51298572e+01,
#         -1.37454674e+01,   8.16724633e+00,  -3.16850352e+00,
#          8.74607042e-01,  -1.07878768e+00,   1.97939820e+00,
#         -8.26149646e-01,  -1.62437297e-01,  -1.45694910e+00,
#          1.42153527e+00,   1.29203135e+02,  -9.25284676e+00,
#          2.63967417e+00,   2.06410900e+00,   6.03258240e-02*2])

start_params.append([ -3.56709315e+00,  -2.97358686e-03,  -4.37632666e+02,
         3.35095381e+02,  -2.95083648e+02,   2.94263473e+02,
        -8.57731610e+01,  -1.62036228e+01,   1.30838141e+01,
        -6.46551376e+00,   8.01826587e+00,  -3.58786095e+00,
         1.25735987e+00,  -1.21627097e+00,   2.04033545e+00,
        -8.04702913e-01,  -1.92666480e-01,  -1.44083371e+00,
         1.41816098e+00,   1.70360405e+02,  -1.89070431e+01,
         7.47139804e+00,   1.20540194e+00,   1.34588181e-01, 0.0])

multi_pars = start_params
print(multi_pars)

[[-3.56709315, -0.00297358686, -437.632666, 335.095381, -295.083648, 294.263473, -85.773161, -16.2036228, 13.0838141, -6.46551376, 8.01826587, -3.58786095, 1.25735987, -1.21627097, 2.04033545, -0.804702913, -0.19266648, -1.44083371, 1.41816098, 170.360405, -18.9070431, 7.47139804, 1.20540194, 0.134588181, 0.0]]


In [17]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars[-1])
    
    #distances = pool.map(get_sd, multi_pars)
    
    distances = [get_sd(multi_pars[-1])]
    
    optimal_params = zip(distances, multi_pars[-1:])
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(50):
        #optimal_params = pool.map(get_opt, m_pars)
        optimal_params = [get_opt(m_pars)]
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [-3.56709315, -0.00297358686, -437.632666, 335.095381, -295.083648, 294.263473, -85.773161, -16.2036228, 13.0838141, -6.46551376, 8.01826587, -3.58786095, 1.25735987, -1.21627097, 2.04033545, -0.804702913, -0.19266648, -1.44083371, 1.41816098, 170.360405, -18.9070431, 7.47139804, 1.20540194, 0.134588181, 0.0])
loss 2.65547228772e-06 2.65547228772e-06 0.0
('Best params:', [(2.6554722877203052e-06, [-3.56709315, -0.00297358686, -437.632666, 335.095381, -295.083648, 294.263473, -85.773161, -16.2036228, 13.0838141, -6.46551376, 8.01826587, -3.58786095, 1.25735987, -1.21627097, 2.04033545, -0.804702913, -0.19266648, -1.44083371, 1.41816098, 170.360405, -18.9070431, 7.47139804, 1.20540194, 0.134588181, 0.0])])
('ieam:', 0)
loss 2.65547228772e-06 2.65547228772e-06 0.0
loss 0.00237354475404 0.00237354475404 0.0
loss 1.37008945195e-05 1.37008945195e-05 0.0
loss 2.65561204841e-06 2.65561204841e-06 0.0
loss 3.35448958896e-06 3.35448958896e-06 0.0
loss 1.32321811946e-05 1.32321

loss 6.16742400945e-06 6.16742400945e-06 0.0
loss 1.86943021636e-05 1.86943021636e-05 0.0
loss 5.82440281338e-06 5.82440281338e-06 0.0
loss 1.54400870254e-05 1.54400870254e-05 0.0
loss 5.45722162895e-06 5.45722162895e-06 0.0
loss 1.64115670562e-05 1.64115670562e-05 0.0
loss 5.3081748822e-06 5.3081748822e-06 0.0
loss 1.70308448516e-05 1.70308448516e-05 0.0
loss 5.06650870501e-06 5.06650870501e-06 0.0
loss 1.73064670968e-05 1.73064670968e-05 0.0
loss 4.92942142135e-06 4.92942142135e-06 0.0
loss 1.57164925312e-05 1.57164925312e-05 0.0
loss 5.03423578269e-06 5.03423578269e-06 0.0
loss 1.797717501e-05 1.797717501e-05 0.0
loss 4.69592343056e-06 4.69592343056e-06 0.0
loss 9.19471453535e-06 9.19471453535e-06 0.0
loss 1.02886810514e-05 1.02886810514e-05 0.0
loss 4.53196226197e-06 4.53196226197e-06 0.0
loss 1.08325178968e-05 1.08325178968e-05 0.0
loss 4.11034377206e-06 4.11034377206e-06 0.0
loss 8.15348719212e-06 8.15348719212e-06 0.0
loss 3.93204658159e-06 3.93204658159e-06 0.0
loss 7.810481956

loss 2.69911545788e-06 2.69911545788e-06 0.0
loss 2.70662614542e-06 2.70662614542e-06 0.0
loss 2.66655050313e-06 2.66655050313e-06 0.0
loss 2.70590977509e-06 2.70590977509e-06 0.0
loss 2.66602559106e-06 2.66602559106e-06 0.0
loss 2.6991451343e-06 2.6991451343e-06 0.0
loss 2.66615789109e-06 2.66615789109e-06 0.0
loss 2.70400289396e-06 2.70400289396e-06 0.0
loss 2.66498383649e-06 2.66498383649e-06 0.0
loss 2.7030419091e-06 2.7030419091e-06 0.0
loss 2.66433937845e-06 2.66433937845e-06 0.0
loss 2.68829186003e-06 2.68829186003e-06 0.0
loss 2.68877839477e-06 2.68877839477e-06 0.0
loss 2.66400180383e-06 2.66400180383e-06 0.0
loss 2.69327009987e-06 2.69327009987e-06 0.0
loss 2.66345179867e-06 2.66345179867e-06 0.0
loss 2.69191405052e-06 2.69191405052e-06 0.0
loss 2.66360319788e-06 2.66360319788e-06 0.0
loss 2.68964319755e-06 2.68964319755e-06 0.0
loss 2.66379793491e-06 2.66379793491e-06 0.0
loss 2.69125267633e-06 2.69125267633e-06 0.0
loss 2.66337260131e-06 2.66337260131e-06 0.0
loss 2.6853293

loss 2.6556235905e-06 2.6556235905e-06 0.0
loss 2.65597737389e-06 2.65597737389e-06 0.0
loss 2.65561243882e-06 2.65561243882e-06 0.0
loss 2.65558130662e-06 2.65558130662e-06 0.0
loss 2.65556050135e-06 2.65556050135e-06 0.0
loss 2.65570617846e-06 2.65570617846e-06 0.0
loss 2.65555986524e-06 2.65555986524e-06 0.0
loss 2.65588809397e-06 2.65588809397e-06 0.0
loss 2.65556619586e-06 2.65556619586e-06 0.0
loss 2.65590510883e-06 2.65590510883e-06 0.0
loss 2.65556316297e-06 2.65556316297e-06 0.0
loss 2.65579827767e-06 2.65579827767e-06 0.0
loss 2.65556559665e-06 2.65556559665e-06 0.0
loss 2.65562522488e-06 2.65562522488e-06 0.0
loss 2.6556639108e-06 2.6556639108e-06 0.0
loss 2.65557287269e-06 2.65557287269e-06 0.0
loss 2.6556718132e-06 2.6556718132e-06 0.0
loss 2.6557210615e-06 2.6557210615e-06 0.0
loss 2.65555074905e-06 2.65555074905e-06 0.0
loss 2.65570302721e-06 2.65570302721e-06 0.0
loss 2.65554643564e-06 2.65554643564e-06 0.0
loss 2.65566895355e-06 2.65566895355e-06 0.0
loss 2.65565935711

loss 2.65547554e-06 2.65547554e-06 0.0
loss 2.65547737988e-06 2.65547737988e-06 0.0
loss 2.65547149804e-06 2.65547149804e-06 0.0
loss 2.65547493653e-06 2.65547493653e-06 0.0
loss 2.65547830635e-06 2.65547830635e-06 0.0
loss 2.65547128492e-06 2.65547128492e-06 0.0
loss 2.65547338029e-06 2.65547338029e-06 0.0
loss 2.65547587999e-06 2.65547587999e-06 0.0
loss 2.65547139442e-06 2.65547139442e-06 0.0
loss 2.65547572573e-06 2.65547572573e-06 0.0
loss 2.65547133772e-06 2.65547133772e-06 0.0
loss 2.65547622311e-06 2.65547622311e-06 0.0
loss 2.65547122387e-06 2.65547122387e-06 0.0
loss 2.65547514692e-06 2.65547514692e-06 0.0
loss 2.65547539929e-06 2.65547539929e-06 0.0
loss 2.65547125021e-06 2.65547125021e-06 0.0
loss 2.65547141938e-06 2.65547141938e-06 0.0
loss 2.65547607483e-06 2.65547607483e-06 0.0
loss 2.65547096892e-06 2.65547096892e-06 0.0
loss 2.65547366265e-06 2.65547366265e-06 0.0
loss 2.65547348533e-06 2.65547348533e-06 0.0
loss 2.65547380449e-06 2.65547380449e-06 0.0
loss 2.655476032

...

loss 2.46714133576e-06 2.46714133576e-06 0.0
loss 2.46714118655e-06 2.46714118655e-06 0.0
loss 2.46714143522e-06 2.46714143522e-06 0.0
loss 2.46714132843e-06 2.46714132843e-06 0.0
loss 2.46714134109e-06 2.46714134109e-06 0.0
loss 2.46714132045e-06 2.46714132045e-06 0.0
loss 2.46714139237e-06 2.46714139237e-06 0.0
loss 2.46714139238e-06 2.46714139238e-06 0.0
loss 2.46714136328e-06 2.46714136328e-06 0.0
loss 2.46714156025e-06 2.46714156025e-06 0.0
loss 2.4671414912e-06 2.4671414912e-06 0.0
loss 2.46714140948e-06 2.46714140948e-06 0.0
loss 2.46714132911e-06 2.46714132911e-06 0.0
loss 2.46714139172e-06 2.46714139172e-06 0.0
loss 2.46714134685e-06 2.46714134685e-06 0.0
loss 2.46714130335e-06 2.46714130335e-06 0.0
loss 2.46714133002e-06 2.46714133002e-06 0.0
loss 2.4671411437e-06 2.4671411437e-06 0.0
loss 2.4671411002e-06 2.4671411002e-06 0.0
loss 2.46714136397e-06 2.46714136397e-06 0.0
loss 2.46714126871e-06 2.46714126871e-06 0.0
loss 2.46714135264e-06 2.46714135264e-06 0.0
loss 2.467141108

loss 2.46713788037e-06 2.46713788037e-06 0.0
loss 2.46713820524e-06 2.46713820524e-06 0.0
loss 2.46713788349e-06 2.46713788349e-06 0.0
loss 2.4671380389e-06 2.4671380389e-06 0.0
loss 2.46713828474e-06 2.46713828474e-06 0.0
loss 2.4671376519e-06 2.4671376519e-06 0.0
loss 2.46713770142e-06 2.46713770142e-06 0.0
loss 2.4671377101e-06 2.4671377101e-06 0.0
loss 2.4671378564e-06 2.4671378564e-06 0.0
loss 2.46713798232e-06 2.46713798232e-06 0.0
loss 2.46713751491e-06 2.46713751491e-06 0.0
loss 2.4671373655e-06 2.4671373655e-06 0.0
loss 2.46713751048e-06 2.46713751048e-06 0.0
loss 2.46713712964e-06 2.46713712964e-06 0.0
loss 2.46713651612e-06 2.46713651612e-06 0.0
loss 2.46713743452e-06 2.46713743452e-06 0.0
loss 2.46713716586e-06 2.46713716586e-06 0.0
loss 2.46713730816e-06 2.46713730816e-06 0.0
loss 2.4671372442e-06 2.4671372442e-06 0.0
loss 2.46713696044e-06 2.46713696044e-06 0.0
loss 2.46713699619e-06 2.46713699619e-06 0.0
loss 2.46713690582e-06 2.46713690582e-06 0.0
loss 2.46713720272e-06

loss 2.46710838598e-06 2.46710838598e-06 0.0
loss 2.46710854478e-06 2.46710854478e-06 0.0
loss 2.46710907367e-06 2.46710907367e-06 0.0
loss 2.46710712365e-06 2.46710712365e-06 0.0
loss 2.46710719274e-06 2.46710719274e-06 0.0
loss 2.46710748067e-06 2.46710748067e-06 0.0
loss 2.4671076359e-06 2.4671076359e-06 0.0
loss 2.46710724713e-06 2.46710724713e-06 0.0
loss 2.46710595546e-06 2.46710595546e-06 0.0
loss 2.46710607757e-06 2.46710607757e-06 0.0
loss 2.46710499178e-06 2.46710499178e-06 0.0
loss 2.46710170595e-06 2.46710170595e-06 0.0
loss 2.46710433784e-06 2.46710433784e-06 0.0
loss 2.46710367466e-06 2.46710367466e-06 0.0
loss 2.46710387577e-06 2.46710387577e-06 0.0
loss 2.46710294008e-06 2.46710294008e-06 0.0
loss 2.46710260813e-06 2.46710260813e-06 0.0
loss 2.46710199621e-06 2.46710199621e-06 0.0
loss 2.46710196822e-06 2.46710196822e-06 0.0
loss 2.46710238369e-06 2.46710238369e-06 0.0
loss 2.46710075918e-06 2.46710075918e-06 0.0
loss 2.46709723156e-06 2.46709723156e-06 0.0
loss 2.46709

loss 2.46707662902e-06 2.46707662902e-06 0.0
loss 2.46707583764e-06 2.46707583764e-06 0.0
loss 2.46707392365e-06 2.46707392365e-06 0.0
loss 2.4670760458e-06 2.4670760458e-06 0.0
loss 2.46707673907e-06 2.46707673907e-06 0.0
loss 2.46707457885e-06 2.46707457885e-06 0.0
loss 2.46707439238e-06 2.46707439238e-06 0.0
loss 2.46707514647e-06 2.46707514647e-06 0.0
loss 2.4670741142e-06 2.4670741142e-06 0.0
loss 2.46707631283e-06 2.46707631283e-06 0.0
loss 2.46707437256e-06 2.46707437256e-06 0.0
loss 2.46707568313e-06 2.46707568313e-06 0.0
loss 2.46707646712e-06 2.46707646712e-06 0.0
loss 2.46707430064e-06 2.46707430064e-06 0.0
loss 2.46707639523e-06 2.46707639523e-06 0.0
loss 2.4670742904e-06 2.4670742904e-06 0.0
loss 2.4670753318e-06 2.4670753318e-06 0.0
loss 2.46707451519e-06 2.46707451519e-06 0.0
loss 2.4670749764e-06 2.4670749764e-06 0.0
loss 2.46707518679e-06 2.46707518679e-06 0.0
loss 2.46707540022e-06 2.46707540022e-06 0.0
loss 2.46707409125e-06 2.46707409125e-06 0.0
loss 2.46707391763e-

loss 2.46707300529e-06 2.46707300529e-06 0.0
loss 2.46707287296e-06 2.46707287296e-06 0.0
loss 2.46707297887e-06 2.46707297887e-06 0.0
loss 2.46707299394e-06 2.46707299394e-06 0.0
loss 2.46707274195e-06 2.46707274195e-06 0.0
loss 2.46707290602e-06 2.46707290602e-06 0.0
loss 2.46707305415e-06 2.46707305415e-06 0.0
loss 2.4670728987e-06 2.4670728987e-06 0.0
loss 2.46707303305e-06 2.46707303305e-06 0.0
loss 2.4670728463e-06 2.4670728463e-06 0.0
loss 2.46707302393e-06 2.46707302393e-06 0.0
loss 2.46707288738e-06 2.46707288738e-06 0.0
loss 2.46707290068e-06 2.46707290068e-06 0.0
loss 2.4670731545e-06 2.4670731545e-06 0.0
loss 2.46707286474e-06 2.46707286474e-06 0.0
loss 2.46707289738e-06 2.46707289738e-06 0.0
loss 2.4670727959e-06 2.4670727959e-06 0.0
loss 2.46707303016e-06 2.46707303016e-06 0.0
loss 2.46707286873e-06 2.46707286873e-06 0.0
loss 2.46707289005e-06 2.46707289005e-06 0.0
loss 2.46707278413e-06 2.46707278413e-06 0.0
loss 2.46707292938e-06 2.46707292938e-06 0.0
loss 2.46707280013

In [60]:
params_output = [(8.9710060363567114e-07, np.array([ -4.18353755e+00,  -9.63668936e-03,  -1.00171035e+02,
         1.90025394e+01,   2.15938317e+01,  -1.39759833e+01,
         2.16332289e+01,  -3.29542126e+00,   1.70455674e+00,
         1.41347064e+00,  -9.02958785e-01,  -8.62309098e-01,
         1.95964588e+00,  -8.70527088e-01,   3.22342700e-02,
        -1.53866121e+00,   1.37095441e+00,  -4.32896107e+01,
         4.64461212e+00,   3.23329113e-01,   5.82061842e-02]))]

In [73]:
params_output = [(8.829397265807305e-07, np.array([ -4.33954858e+00,  -1.02215197e-02,  -1.12590032e+02,
         3.06702045e+01,   1.74951979e+01,  -1.33298120e+01,
         2.13899957e+01,  -3.70881631e+00,   1.56452640e+00,
         1.27789071e+00,  -8.54623702e-01,  -8.39818015e-01,
         1.95990543e+00,  -8.75948596e-01,   1.81927625e-02,
        -1.54683863e+00,   1.38614460e+00,  -4.28747460e+01,
         4.18974818e+00,   1.56622590e-01,   5.72961538e-02,
         3.46319317e+00]))]

In [114]:
params_output = [(8.7421414571196454e-07, np.array([ -4.31249172e+00,  -9.93971047e-03,  -3.76018390e+01,
        -1.14759006e+02,   1.72557600e+01,   2.66437414e+01,
        -1.50817090e+01,   2.22342349e+01,  -3.62963119e+00,
         1.62230813e+00,   1.18480877e+00,  -8.52354746e-01,
        -8.38460594e-01,   1.98957701e+00,  -8.86622667e-01,
         1.66082225e-03,  -1.54824194e+00,   1.39761513e+00,
        -5.06767503e+01,   4.47029066e+00,   9.10205250e-02,
         5.87302830e-02,   1.82639066e+00]))]

In [39]:
params_output = [(8.8257346852300666e-07, np.array([ -4.36548916e+00,  -1.11867827e-02,  -1.94093020e+01,
        -1.40195282e+02,   4.53864231e+01,   1.49756180e+01,
        -1.36031385e+01,   2.21581200e+01,  -4.61501041e+00,
         2.06360250e+00,   1.12795645e+00,  -8.01200744e-01,
        -8.58426028e-01,   1.95860157e+00,  -8.68817546e-01,
         2.43936831e-02,  -1.54555297e+00,   1.38005891e+00,
        -5.22754243e+01,   3.98209114e+00,   3.07369702e-01,
         5.51658454e-02,   1.58601447e+00]))]

In [40]:
params_output = [(2.8925274000958436e-06, np.array([ -3.09187534e+00,   1.19622206e-04,  -5.67875917e+02,
         3.21802084e+02,  -4.71317094e+02,   3.98296604e+02,
        -1.13270858e+02,   6.03114401e+00,   1.48067908e+01,
        -1.57531660e+01,   7.80863462e+00,  -2.99246651e+00,
         7.33596451e-01,  -9.50794219e-01,   1.94186078e+00,
        -8.83596676e-01,  -1.33608784e-01,  -1.46694544e+00,
         1.42447434e+00,   7.53865380e+01,   3.29733034e-01,
         2.18327852e+00,   6.63152141e-02]))]

In [62]:
# convert lists of optimal parameters to dictionaries
params_optimal = []
for pars in params_output:
    #params_optimal.append(to_param_dict(pars, [2, 15, 4, 0]))
    params_optimal.append(to_param_dict(pars[1], stats['hyperparams']))

In [64]:
# store hyperparameters and output parameters in a single file
try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

no file


In [65]:
with open(os.path.join(working, 'params_store' + '.pickle'), 'rb') as fi:
    retreived_params = pickle.load(fi)  

In [66]:
retreived_params

[{'hyperparams': {u'edens': [2.5, 3.1000000000000001, 3.5, 4.9000000000000004],
   u'pair': [2.5648974999999998,
    2.6297950000000001,
    2.6946924999999999,
    2.8663175000000001,
    2.9730449999999999,
    3.0797724999999998,
    3.5164724999999999,
    3.8464450000000001,
    4.1764175000000003,
    4.7008450000000002,
    4.8952999999999998,
    5.0897550000000003,
    5.3429525,
    5.4016950000000001,
    5.4604375000000003]},
  'params': {'edens': array([-43.2896107 ,   4.64461212,   0.32332911,   0.05820618]),
   'embed': array([-4.18353755, -0.00963669]),
   'lrcorr': array([], dtype=float64),
   'pair': array([ -1.00171035e+02,   1.90025394e+01,   2.15938317e+01,
           -1.39759833e+01,   2.16332289e+01,  -3.29542126e+00,
            1.70455674e+00,   1.41347064e+00,  -9.02958785e-01,
           -8.62309098e-01,   1.95964588e+00,  -8.70527088e-01,
            3.22342700e-02,  -1.53866121e+00,   1.37095441e+00])}}]